In [1]:
import pygame
import sys
import math
import numpy as np
import random
import heapq
from collections import deque

########################
# GAME CONFIGURATIONS
########################

BOARD_SIZE = 8           # NxN Hex board
CELL_RADIUS = 25          # Pixel radius of each hex cell
CELL_GAP = 3              # Gap between hex cells
BACKGROUND_COLOR = (230, 230, 230)
RED_COLOR = (220, 20, 60)
BLUE_COLOR = (30, 144, 255)
EMPTY_COLOR = (200, 200, 200)
LINE_COLOR = (50, 50, 50)

WINDOW_TITLE = "Hex (John Nash's Game)"
FPS = 30


########################
# HELPER FUNCTIONS
########################

def create_board(n):
    """
    Create the NxN board. 
    Each cell is 0=empty, 1=red, 2=blue.
    """
    return [[0 for _ in range(n)] for _ in range(n)]


def get_hex_center(row, col):
    """
    Return the (x, y) center in screen coordinates for the hex 
    at (row, col). We'll do an axial-like layout where each row 
    is shifted horizontally relative to the previous row.
    """
    # Vertical spacing between rows
    vert_spacing = CELL_RADIUS * 1.5
    
    # Horizontal spacing (including some shift per row)
    horiz_spacing = (CELL_RADIUS * 2) - CELL_GAP
    
    # X offset for staggering the rows
    x_offset = col * horiz_spacing + row * (CELL_RADIUS)
    
    # Y offset: row index times vertical spacing
    y_offset = row * vert_spacing
    
    # You can fine-tune for aesthetics
    return (50 + x_offset, 50 + y_offset)


def draw_board(screen, board):
    """
    Draw the entire board (hexes + occupant).
    """
    screen.fill(BACKGROUND_COLOR)
    n = len(board)

    for r in range(n):
        for c in range(n):
            center = get_hex_center(r, c)
            color = EMPTY_COLOR
            if board[r][c] == 1:
                color = RED_COLOR
            elif board[r][c] == 2:
                color = BLUE_COLOR
            
            # Draw the hexagon using a small approximation with 6 lines.
            draw_hex_cell(screen, center, CELL_RADIUS, color)

    #draw red and blue rectangles at the border of the game board   
    
    board_width = (CELL_RADIUS - .5)*CELL_GAP*BOARD_SIZE*.7
    board_height = (CELL_RADIUS - .5)*CELL_GAP*BOARD_SIZE*.6
    
    #top blue rectangle
    pygame.draw.polygon(screen, BLUE_COLOR, 
        (
            (CELL_RADIUS * .5, 
                CELL_RADIUS * .5), 
            (CELL_RADIUS + board_width, 
                CELL_RADIUS * .5), 
            (CELL_RADIUS + board_width, 
                CELL_RADIUS + 1), 
            (CELL_RADIUS * .5, 
                CELL_RADIUS + 1), 
        )
    )
    
    #bottom blue rectangle
    pygame.draw.polygon(screen, BLUE_COLOR, 
        (
            (CELL_RADIUS * .5 + board_width/2, 
                CELL_RADIUS * .5 + board_height), 
            (CELL_RADIUS + board_width + board_width/2, 
                CELL_RADIUS * .5 + board_height), 
            (CELL_RADIUS + board_width + board_width/2, 
                CELL_RADIUS + 1 + board_height), 
            (CELL_RADIUS * .5 + board_width/2, 
                CELL_RADIUS + 1 + board_height), 
        )
    )
    
    #left red rectangle
    pygame.draw.polygon(screen, RED_COLOR, 
        (
            (-5 + CELL_RADIUS * .5, 
                CELL_RADIUS * .5), 
            (CELL_RADIUS * .5 + board_width/2, 
                CELL_RADIUS * .5 + board_height), 
            (CELL_RADIUS * .5 + board_width/2 + 5, 
                CELL_RADIUS * .5 + board_height), 
            (-5 + CELL_RADIUS * .5 + 5, 
                CELL_RADIUS * .5), 
        )
    )
    
    #right red rectangle
    pygame.draw.polygon(screen, RED_COLOR, 
        (
            (CELL_RADIUS * .5 + board_width, 
                CELL_RADIUS * .5), 
            (CELL_RADIUS * .5 + board_width + board_width/2, 
                CELL_RADIUS * .5 + board_height), 
            (CELL_RADIUS * .5 + board_width + board_width/2 + 5, 
                CELL_RADIUS * .5 + board_height), 
            (CELL_RADIUS * .5 + 5 + board_width, 
                CELL_RADIUS * .5), 
        )
    )
    
    
    pygame.display.flip()
    


def draw_hex_cell(screen, center, radius, fill_color):
    """
    Draws a single hex cell given its center, radius, and color.
    We'll draw a filled polygon and an outline.
    """
    x0, y0 = center
    # Hexagon points
    points = []
    for i in range(6):
        angle_deg = 60 * i - 30  # shift so top side is flat
        angle_rad = 3.14159 / 180.0 * angle_deg
        x = x0 + radius * 1.0 * math.cos(angle_rad)
        y = y0 + radius * 1.0 * math.sin(angle_rad)
        points.append((x, y))

    pygame.draw.polygon(screen, fill_color, points)       # filled
    pygame.draw.polygon(screen, LINE_COLOR, points, width=2)  # outline


def get_clicked_cell(pos, board):
    """
    Given a mouse position `pos`, find the closest hex cell 
    if it's within some threshold. 
    """
    x_click, y_click = pos
    n = len(board)
    closest = None
    min_dist_sq = float('inf')
    threshold = CELL_RADIUS * 1.2  # a bit more than radius

    for r in range(n):
        for c in range(n):
            center = get_hex_center(r, c)
            dx = x_click - center[0]
            dy = y_click - center[1]
            dist_sq = dx*dx + dy*dy
            if dist_sq < min_dist_sq:
                min_dist_sq = dist_sq
                closest = (r, c)
    
    # If the closest is within threshold distance, return it
    if min_dist_sq <= threshold**2:
        return closest
    else:
        return None


def check_winner(board):
    """
    Check if there's a winner:
    - Red (1) tries to connect LEFT to RIGHT
    - Blue (2) tries to connect TOP to BOTTOM
    
    We'll do BFS for each side's edges.
    Return 1 if Red wins, 2 if Blue wins, or 0 if no winner yet.
    """
    n = len(board)
    # Check red: from any cell in left column to any in right column
    if has_path(board, player=1, starts=[(r, 0) for r in range(n) if board[r][0] == 1],
                is_goal=lambda r, c: c == n-1):
        return 1

    # Check blue: from any cell in top row to any in bottom row
    if has_path(board, player=2, starts=[(0, c) for c in range(n) if board[0][c] == 2],
                is_goal=lambda r, c: r == n-1):
        return 2

    return 0


def has_path(board, player, starts, is_goal):
    """
    General BFS to see if there's a path for `player`'s stones
    from the given start cells to a cell where `is_goal(r, c)` is True.
    """
    n = len(board)
    visited = set()
    q = deque()

    for s in starts:
        q.append(s)
        visited.add(s)

    while q:
        r, c = q.popleft()
        if is_goal(r, c):
            return True
        
        for nr, nc in neighbors(r, c, n):
            if (nr, nc) not in visited and board[nr][nc] == player:
                visited.add((nr, nc))
                q.append((nr, nc))

    return False


def neighbors(r, c, n):
    """
    Return the 6 valid neighbors for a hex cell (r, c).
    """
    deltas = [(-1, 0), (-1, 1), (0, -1),
              (0, 1), (1, -1), (1, 0)]
    for dr, dc in deltas:
        rr = r + dr
        cc = c + dc
        if 0 <= rr < n and 0 <= cc < n:
            yield rr, cc


########################
# MAIN GAME LOOP
########################

def main():
    pygame.init()
    # Rough estimate for window size
    width = 800
    height = 600
    screen = pygame.display.set_mode((width, height))
    pygame.display.set_caption(WINDOW_TITLE)
    clock = pygame.time.Clock()

    board = create_board(BOARD_SIZE)
    current_player = 1  # 1=Red, 2=Blue
    game_over = False
    winner = 0

    draw_board(screen, board)
    
    #delay between moves
    num_milliseconds = 500
    MOVEEVENT, t, trail = pygame.USEREVENT+1, num_milliseconds, []
    pygame.time.set_timer(MOVEEVENT, t)

    while True:
        clock.tick(FPS)
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                pygame.quit()
                sys.exit()

            if event.type == pygame.MOUSEBUTTONDOWN and not game_over:
                cell = get_clicked_cell(event.pos, board)
                if cell is not None:
                    r, c = cell
                    # If empty, place current player's stone
                    if board[r][c] == 0:
                        board[r][c] = current_player
                        # Check for winner
                        winner = check_winner(board)
                        if winner != 0:
                            game_over = True
                        else:
                            # Switch player
                            current_player = 2 if current_player == 1 else 1
                draw_board(screen, board)
                
            if event.type == MOVEEVENT: # is called every 't' milliseconds
                # make a move
                
                board_array = np.array(board)
                unvisited = np.where(board_array == 0)
                if len(unvisited) > 0:
                    # then there is some legal move to make
                    try:
                        if current_player == 1:
                            #then it is red's turn to move
                            x_move, y_move = player_one(board_array, unvisited)
                            board[x_move][y_move] = current_player
                        else:
                            #then it is blue's turn to move
                            x_move, y_move = player_two(board_array, unvisited)
                            board[x_move][y_move] = current_player
                            
                        
                        winner = check_winner(board)
                        if winner != 0:
                            game_over = True
                        else:
                            # Switch player
                            current_player = 2 if current_player == 1 else 1
                    
                        draw_board(screen, board)
                    except:
                        print('the game is over.')
                        #pygame.quit()
                        #sys.exit()
                        

        # If game over, display winner text
        if game_over:
            font = pygame.font.SysFont(None, 48)
            if winner == 1:
                msg = "Red wins!"
                color = RED_COLOR
            else:
                msg = "Blue wins!"
                color = BLUE_COLOR
            text = font.render(msg, True, color)
            rect = text.get_rect(center=(width // 2, 30))
            screen.blit(text, rect)
            pygame.display.flip()
            
            
###################################
# DEFINE PLAYER ONE STRATEGY HERE #
###################################

def player_one(board_array, unvisited):
    # board_array is a square numpy array showing the current state of the game
    #     where 0 is an unplayed hex, 1 is a red-occupied hex, and 2 is a blue-occupied hex
    # unvisited is a tuple of arrays of x and y indices of unplayed hex cells
    # player_one should output the x,y indices of the next move to make
    return block_player(board_array)

def blue_connectivity_cost(board):
    """
    Compute the "connectivity cost" for blue (player 2) to connect the top
    to the bottom of the board. We assume blue can play on empty cells (cost 1)
    and already has blue stones (cost 0); red cells (value 1) are blocked.
    We use a Dijkstra-style algorithm on the n×n grid (with hex neighborhood).
    
    Returns the minimum cost to reach any cell in the bottom row, or np.inf
    if no path exists.
    """
    n = board.shape[0]
    cost = np.full((n, n), np.inf)
    heap = []
    
    # For a hex board, a standard choice for neighbors (for a 2D array representation)
    directions = [(-1, 0), (-1, 1), (0, -1), (0, 1), (1, -1), (1, 0)]
    
    # Initialize the top row (row 0) as sources, if they are not red (blocked).
    # The cost to "enter" a cell is 0 if it is already blue (2) and 1 if empty (0).
    for j in range(n):
        if board[0, j] != 1:  # not red
            initial = 0 if board[0, j] == 2 else 1
            cost[0, j] = initial
            heapq.heappush(heap, (initial, (0, j)))
    
    while heap:
        cur_cost, (i, j) = heapq.heappop(heap)
        if cur_cost > cost[i, j]:
            continue
        # If we reached the bottom row, return the cost.
        if i == n - 1:
            return cur_cost
        # Relax neighbors.
        for di, dj in directions:
            ni, nj = i + di, j + dj
            if 0 <= ni < n and 0 <= nj < n:
                if board[ni, nj] == 1:
                    continue  # red cell: blocked
                # Cost to enter neighbor: 0 if already blue, 1 if empty.
                next_cost = cur_cost + (0 if board[ni, nj] == 2 else 1)
                if next_cost < cost[ni, nj]:
                    cost[ni, nj] = next_cost
                    heapq.heappush(heap, (next_cost, (ni, nj)))
    return np.inf

def block_player(board):
    """
    Given an n×n numpy array representing a Hex board:
       0: empty hex,
       1: red player's stone,
       2: blue player's stone,
    return a tuple (i, j) representing the next move for red (player 1).
    
    The strategy is to "block" blue's best move. In particular, for every empty
    cell we simulate a blue move (i.e. set that cell to 2) and compute the blue
    connectivity cost (the minimal number of moves blue needs to connect top and bottom).
    We then choose the empty cell that minimizes this cost, provided it improves blue’s
    situation relative to the current board. If no empty cell improves blue's connectivity,
    we choose a random empty cell.
    """
    n = board.shape[0]
    empty_cells = [(i, j) for i in range(n) for j in range(n) if board[i, j] == 0]
    if not empty_cells:
        return None  # board is full
    
    # Compute blue's current connectivity cost.
    base_cost = blue_connectivity_cost(board)
    
    best_move = None
    best_cost = np.inf
    for (i, j) in empty_cells:
        board_copy = board.copy()
        board_copy[i, j] = 2  # simulate blue playing here
        cost = blue_connectivity_cost(board_copy)
        if cost < best_cost:
            best_cost = cost
            best_move = (i, j)
    
    # If playing the best move for blue would improve blue's connectivity (i.e. lower cost)
    # compared to the current board, then block that move.
    if best_cost < base_cost:
        return best_move
    else:
        # No clear "threatening" move found; choose a random empty cell.
        return random.choice(empty_cells)



###################################
# DEFINE PLAYER TWO STRATEGY HERE #
###################################

def player_two(board_array, unvisited):
    num_unvisited = len(unvisited[0])
    random_int = random.randint(0, num_unvisited - 1)
    random_x = unvisited[0][random_int]
    random_y = unvisited[1][random_int]
    return random_x, random_y


##############################

if __name__ == "__main__":
    main()


pygame 2.6.1 (SDL 2.28.4, Python 3.11.7)
Hello from the pygame community. https://www.pygame.org/contribute.html


SystemExit: 

C:\Users\steve\anaconda3\Lib\site-packages\IPython\core\interactiveshell.py:3561: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
